In [1]:
import pandas as pd
import numpy as np

In [2]:
# Read ratings data
df = pd.read_csv('ml-1m/movies.dat', sep='::', engine='python', names=['MovieID', 'Title', 'Genres'], encoding='latin-1')
df1 = pd.read_csv('ml-1m/ratings.dat', sep='::', engine='python', names=['UserID', 'MovieID', 'Rating', 'Timestamp'], encoding='latin-1')
df2 = pd.read_csv('ml-1m/users.dat', sep='::', engine='python', names=['UserID', 'Gender', 'Age', 'Occupation', 'Zip-code'], encoding='latin-1')


In [3]:
df.shape

(3883, 3)

In [4]:
df1.shape

(1000209, 4)

In [5]:
df2.shape

(6040, 5)

In [6]:
df.sample(2)


MovieID                           Title                       Genres
1977     2046  Flight of the Navigator (1986)  Adventure|Children's|Sci-Fi
2184     2253                     Toys (1992)        Action|Comedy|Fantasy

In [7]:
df1.sample(2)

UserID  MovieID  Rating  Timestamp
707824    4241     2987       4  983483283
279440    1680     3146       1  974837728

In [8]:
df2.sample(2)

UserID Gender  Age  Occupation Zip-code
2569    2570      F   56          14    95005
3564    3565      M   25          18    53572

In [9]:
# Extract year from Title column
df['Year'] = df['Title'].str.extract(r'\((\d{4})\)', expand=False)
df.sample(5)

MovieID                                              Title  \
137       139                                      Target (1995)   
3068     3137                             Sea Wolves, The (1980)   
3460     3529             Postman Always Rings Twice, The (1981)   
2862     2931        Time of the Gypsies (Dom za vesanje) (1989)   
3307     3376  Fantastic Night, The (La Nuit Fantastique) (1949)   

              Genres  Year  
137     Action|Drama  1995  
3068      Action|War  1980  
3460  Crime|Thriller  1981  
2862           Drama  1989  
3307         Romance  1949

In [10]:
# Drop Title from df and Zip-code from df2
df_clean = df.drop('Title', axis=1)
df2_clean = df2.drop('Zip-code', axis=1)

# Merge df1 (ratings) with df_clean (movies) on MovieID
merged_df = df1.merge(df_clean, on='MovieID', how='left')

# Merge with df2_clean (users) on UserID
merged_df = merged_df.merge(df2_clean, on='UserID', how='left')

print(f"Original df1 shape: {df1.shape}")
print(f"Merged dataframe shape: {merged_df.shape}")
merged_df.sample(5)

Original df1 shape: (1000209, 4)
Merged dataframe shape: (1000209, 9)


UserID  MovieID  Rating  Timestamp                        Genres  \
242805    1465     3873       4  974766887                Comedy|Western   
336159    1980     3506       3  974687643                  Comedy|Drama   
942494    5685      327       3  958603768  Action|Comedy|Musical|Sci-Fi   
648870    3909     3785       4  965756451                 Comedy|Horror   
285078    1701        6       5  974708550         Action|Crime|Thriller   

        Year Gender  Age  Occupation  
242805  1965      M   50          16  
336159  1979      M   35           7  
942494  1995      M   25          17  
648870  2000      M   18          17  
285078  1995      F   25           4

In [11]:
merged_df.drop('Timestamp', axis=1, inplace=True)

In [12]:
merged_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000209 entries, 0 to 1000208
Data columns (total 8 columns):
 #   Column      Non-Null Count    Dtype 
---  ------      --------------    ----- 
 0   UserID      1000209 non-null  int64 
 1   MovieID     1000209 non-null  int64 
 2   Rating      1000209 non-null  int64 
 3   Genres      1000209 non-null  object
 4   Year        1000209 non-null  object
 5   Gender      1000209 non-null  object
 6   Age         1000209 non-null  int64 
 7   Occupation  1000209 non-null  int64 
dtypes: int64(5), object(3)
memory usage: 61.0+ MB


In [13]:
# 1. Binary encode Gender (M=1, F=0)
merged_df['Gender'] = merged_df['Gender'].map({'M': 1, 'F': 0})

# 2. One-hot encode Age (categorical)
age_dummies = pd.get_dummies(merged_df['Age'], prefix='Age', dtype=int)
merged_df = pd.concat([merged_df, age_dummies], axis=1)
merged_df.drop('Age', axis=1, inplace=True)

print(f"Final merged_df shape: {merged_df.shape}")


Final merged_df shape: (1000209, 14)


In [14]:
merged_df.sample()

UserID  MovieID  Rating                    Genres  Year  Gender  \
275938    1671     1248       4  Crime|Film-Noir|Thriller  1958       1   

        Occupation  Age_1  Age_18  Age_25  Age_35  Age_45  Age_50  Age_56  
275938           0      0       0       0       1       0       0       0

In [15]:
# Remove all Occupation columns (including Occupation_0, Occupation_1, etc.)
occupation_cols = [col for col in merged_df.columns if 'Occupation' in col]
if occupation_cols:
    merged_df.drop(occupation_cols, axis=1, inplace=True)
    print(f"Dropped columns: {occupation_cols}")
else:
    print("No Occupation columns found")
    
print(f"Shape after removing Occupation columns: {merged_df.shape}")
merged_df.head()

Dropped columns: ['Occupation']
Shape after removing Occupation columns: (1000209, 13)


UserID  MovieID  Rating                        Genres  Year  Gender  Age_1  \
0       1     1193       5                         Drama  1975       0      1   
1       1      661       3  Animation|Children's|Musical  1996       0      1   
2       1      914       3               Musical|Romance  1964       0      1   
3       1     3408       4                         Drama  2000       0      1   
4       1     2355       5   Animation|Children's|Comedy  1998       0      1   

   Age_18  Age_25  Age_35  Age_45  Age_50  Age_56  
0       0       0       0       0       0       0  
1       0       0       0       0       0       0  
2       0       0       0       0       0       0  
3       0       0       0       0       0       0  
4       0       0       0       0       0       0

In [16]:
# Import required libraries for modeling
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import matplotlib.pyplot as plt
import seaborn as sns

In [17]:
# Check for any missing values
print("Missing values:")
print(merged_df.isnull().sum())
print(f"\nDataset shape: {merged_df.shape}")
merged_df.head(1)

Missing values:
UserID     0
MovieID    0
Rating     0
Genres     0
Year       0
Gender     0
Age_1      0
Age_18     0
Age_25     0
Age_35     0
Age_45     0
Age_50     0
Age_56     0
dtype: int64

Dataset shape: (1000209, 13)


UserID  MovieID  Rating Genres  Year  Gender  Age_1  Age_18  Age_25  \
0       1     1193       5  Drama  1975       0      1       0       0   

   Age_35  Age_45  Age_50  Age_56  
0       0       0       0       0

## Feature Engineering - Adding More Predictive Features

Let's add more features to improve model accuracy:
1. **Genre features**: One-hot encode movie genres
2. **User statistics**: Average rating per user, rating count
3. **Movie statistics**: Average rating per movie, popularity

In [18]:
# 1. ADD GENRE FEATURES - One-hot encode the genres
# Split genres and create binary columns for each genre
genres_split = merged_df['Genres'].str.get_dummies('|')
print(f"Number of unique genres: {genres_split.shape[1]}")
print(f"Genres: {list(genres_split.columns)}")

# Add genre columns to merged_df
merged_df_enhanced = pd.concat([merged_df, genres_split], axis=1)

# 2. ADD USER STATISTICS
# Calculate average rating per user and number of ratings
user_stats = merged_df.groupby('UserID').agg({
    'Rating': ['mean', 'count', 'std']
}).reset_index()
user_stats.columns = ['UserID', 'User_Avg_Rating', 'User_Rating_Count', 'User_Rating_Std']
user_stats['User_Rating_Std'].fillna(0, inplace=True)  # Fill NaN std for users with 1 rating

# Merge user stats
merged_df_enhanced = merged_df_enhanced.merge(user_stats, on='UserID', how='left')

# 3. ADD MOVIE STATISTICS
# Calculate average rating per movie and number of ratings (popularity)
movie_stats = merged_df.groupby('MovieID').agg({
    'Rating': ['mean', 'count', 'std']
}).reset_index()
movie_stats.columns = ['MovieID', 'Movie_Avg_Rating', 'Movie_Rating_Count', 'Movie_Rating_Std']
movie_stats['Movie_Rating_Std'].fillna(0, inplace=True)

# Merge movie stats
merged_df_enhanced = merged_df_enhanced.merge(movie_stats, on='MovieID', how='left')

print(f"\nOriginal merged_df shape: {merged_df.shape}")
print(f"Enhanced dataset shape: {merged_df_enhanced.shape}")
print(f"\nNew features added: {merged_df_enhanced.shape[1] - merged_df.shape[1]}")

# Show sample
merged_df_enhanced.sample(2)

Number of unique genres: 18
Genres: ['Action', 'Adventure', 'Animation', "Children's", 'Comedy', 'Crime', 'Documentary', 'Drama', 'Fantasy', 'Film-Noir', 'Horror', 'Musical', 'Mystery', 'Romance', 'Sci-Fi', 'Thriller', 'War', 'Western']

Original merged_df shape: (1000209, 13)
Enhanced dataset shape: (1000209, 37)

New features added: 24


UserID  MovieID  Rating                   Genres  Year  Gender  Age_1  \
615907    3728      953       3                    Drama  1946       1      0   
651463    3929     1373       1  Action|Adventure|Sci-Fi  1989       1      0   

        Age_18  Age_25  Age_35  ...  Sci-Fi  Thriller  War  Western  \
615907       1       0       0  ...       0         0    0        0   
651463       0       1       0  ...       1         0    0        0   

        User_Avg_Rating  User_Rating_Count  User_Rating_Std  Movie_Avg_Rating  \
615907         3.875000                 64         0.863731          4.299040   
651463         3.027778                612         1.144637          2.748777   

        Movie_Rating_Count  Movie_Rating_Std  
615907                 729          0.905424  
651463                 613          1.152797  

[2 rows x 37 columns]

In [19]:
# Prepare ENHANCED features (X) and target (y) with all new features

# Convert Year to numeric (handle missing values)
merged_df_enhanced['Year'] = pd.to_numeric(merged_df_enhanced['Year'], errors='coerce')
merged_df_enhanced['Year'].fillna(merged_df_enhanced['Year'].median(), inplace=True)

# Drop non-feature columns
X_enhanced = merged_df_enhanced.drop(['Rating', 'UserID', 'MovieID', 'Genres'], axis=1)
y_enhanced = merged_df_enhanced['Rating']

print(f"Enhanced Features shape: {X_enhanced.shape}")
print(f"Target shape: {y_enhanced.shape}")
print(f"\nTotal features: {X_enhanced.shape[1]}")
print(f"Feature columns: {list(X_enhanced.columns)}")

Enhanced Features shape: (1000209, 33)
Target shape: (1000209,)

Total features: 33
Feature columns: ['Year', 'Gender', 'Age_1', 'Age_18', 'Age_25', 'Age_35', 'Age_45', 'Age_50', 'Age_56', 'Action', 'Adventure', 'Animation', "Children's", 'Comedy', 'Crime', 'Documentary', 'Drama', 'Fantasy', 'Film-Noir', 'Horror', 'Musical', 'Mystery', 'Romance', 'Sci-Fi', 'Thriller', 'War', 'Western', 'User_Avg_Rating', 'User_Rating_Count', 'User_Rating_Std', 'Movie_Avg_Rating', 'Movie_Rating_Count', 'Movie_Rating_Std']


In [20]:
# Split enhanced data into train and test sets (80-20 split)
X_train_enh, X_test_enh, y_train_enh, y_test_enh = train_test_split(
    X_enhanced, y_enhanced, test_size=0.2, random_state=42, stratify=y_enhanced
)

print(f"Enhanced Training set size: {X_train_enh.shape[0]}")
print(f"Enhanced Test set size: {X_test_enh.shape[0]}")
print(f"Number of features: {X_train_enh.shape[1]}")

Enhanced Training set size: 800167
Enhanced Test set size: 200042
Number of features: 33


## 🔧 Feature Engineering Summary

### What is Feature Engineering?
Feature engineering is the process of creating new meaningful features from raw data to improve model performance. We transformed our basic rating data into a rich feature set that captures user preferences, movie characteristics, and behavioral patterns.

---

### 🎯 Features We Created:

#### 1️⃣ **Genre Features** (One-Hot Encoding)
- **Original**: Single column with pipe-separated genres (e.g., "Action|Thriller")
- **Transformed**: 18 binary columns (one per genre)
- **Examples**: `Action`, `Comedy`, `Drama`, `Thriller`, `Romance`, etc.
- **Purpose**: Helps model understand which movie genres user prefers
- **Impact**: +18 features

#### 2️⃣ **User Statistics** (Aggregated Features)
Created 3 features per user based on their rating history:
- **`User_Avg_Rating`**: Average rating given by user (identifies harsh vs generous raters)
- **`User_Rating_Count`**: Total number of movies rated (active vs casual users)
- **`User_Rating_Std`**: Standard deviation of ratings (consistent vs varied taste)
- **Purpose**: Captures user behavior patterns
- **Impact**: +3 features

#### 3️⃣ **Movie Statistics** (Aggregated Features)
Created 3 features per movie based on all user ratings:
- **`Movie_Avg_Rating`**: Average rating received (movie quality indicator)
- **`Movie_Rating_Count`**: Number of ratings (popularity indicator)
- **`Movie_Rating_Std`**: Rating variance (polarizing vs universally liked)
- **Purpose**: Captures movie characteristics and popularity
- **Impact**: +3 features

#### 4️⃣ **Existing Features** (Already Encoded)
- **Gender**: Binary (Male=1, Female=0)
- **Age**: One-hot encoded (7 age groups)
- **Year**: Numeric movie release year

---

### 📊 Feature Engineering Impact:

| Metric | Before | After | Improvement |
|--------|--------|-------|-------------|
| **Total Features** | 9 | 33 | +267% |
| **Feature Types** | Demographics only | Demographics + Preferences + Statistics | Rich context |
| **Model Understanding** | Basic | Deep patterns | Better predictions |

---

### 💡 Why This Improves Accuracy:

1. **User Preferences**: Genre features tell us what types of movies a user likes
2. **User Behavior**: User stats reveal rating patterns (strict rater? movie buff?)
3. **Movie Quality**: Movie stats indicate if a movie is good/popular/polarizing
4. **Interactions**: Model learns combinations (e.g., "harsh users rate popular comedies higher")

**Result**: The model can now predict ratings much more accurately by understanding both the user's taste and the movie's characteristics!

In [21]:
## 🤖 Train Models for Movie Recommendation

# Now let's train KNN and Random Forest models to predict ratings and recommend movies

In [22]:
# Train Random Forest Classifier
print("Training Random Forest model...")
rf_model = RandomForestClassifier(
    n_estimators=100, 
    max_depth=15,
    random_state=42, 
    n_jobs=-1,
    verbose=1
)
rf_model.fit(X_train_enh, y_train_enh)

# Make predictions on test set
rf_pred = rf_model.predict(X_test_enh)
rf_accuracy = accuracy_score(y_test_enh, rf_pred)

print(f"\n✓ Random Forest Accuracy: {rf_accuracy:.4f} ({rf_accuracy*100:.2f}%)")

Training Random Forest model...


[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  26 tasks      | elapsed:   11.4s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:   37.8s finished
[Parallel(n_jobs=12)]: Using backend ThreadingBackend with 12 concurrent workers.
[Parallel(n_jobs=12)]: Done  26 tasks      | elapsed:    0.3s



✓ Random Forest Accuracy: 0.4608 (46.08%)


[Parallel(n_jobs=12)]: Done 100 out of 100 | elapsed:    1.0s finished


In [23]:
# Train KNN Classifier
print("Training KNN model...")
knn_model = KNeighborsClassifier(
    n_neighbors=10,  # Increased for better predictions
    n_jobs=-1
)
knn_model.fit(X_train_enh, y_train_enh)

# Make predictions on test set
knn_pred = knn_model.predict(X_test_enh)
knn_accuracy = accuracy_score(y_test_enh, knn_pred)

print(f"\n✓ KNN Accuracy: {knn_accuracy:.4f} ({knn_accuracy*100:.2f}%)")

Training KNN model...

✓ KNN Accuracy: 0.3472 (34.72%)


## 🎬 Movie Recommendation System

Create a function to recommend top 5 movies for any user

In [24]:
def recommend_movies(user_id, model, model_name, top_n=5):
    """
    Recommend top N movies for a given user based on predicted ratings
    
    Parameters:
    - user_id: User ID to generate recommendations for
    - model: Trained ML model (Random Forest or KNN)
    - model_name: Name of the model for display
    - top_n: Number of movies to recommend (default=5)
    
    Returns:
    - DataFrame with top N movie recommendations
    """
    
    # Get user's existing ratings from enhanced dataframe
    user_data = merged_df_enhanced[merged_df_enhanced['UserID'] == user_id]
    
    if len(user_data) == 0:
        print(f"❌ User {user_id} not found in dataset")
        return None
    
    # Get movies user has already rated
    rated_movies = set(user_data['MovieID'].values)
    
    # Get all movies
    all_movies = set(merged_df_enhanced['MovieID'].unique())
    
    # Find unrated movies
    unrated_movies = list(all_movies - rated_movies)
    
    print(f"\n{'='*70}")
    print(f"🎬 {model_name} - Top {top_n} Movie Recommendations for User {user_id}")
    print(f"{'='*70}")
    print(f"User has rated: {len(rated_movies)} movies")
    print(f"Evaluating: {len(unrated_movies)} unrated movies")
    print(f"{'='*70}\n")
    
    # Get user's feature vector (use first row as template)
    user_features = user_data.iloc[0][X_enhanced.columns].to_dict()
    
    # Predict ratings for all unrated movies
    predictions = []
    
    for movie_id in unrated_movies:
        # Get movie data
        movie_data = merged_df_enhanced[merged_df_enhanced['MovieID'] == movie_id].iloc[0]
        
        # Create feature vector: combine user features with movie-specific features
        features = user_features.copy()
        
        # Update with movie-specific features (genres, year, movie stats)
        for col in X_enhanced.columns:
            if col in ['Year', 'Movie_Avg_Rating', 'Movie_Rating_Count', 'Movie_Rating_Std'] or \
               col in merged_df_enhanced.columns and col not in ['UserID', 'MovieID', 'Rating', 'Genres']:
                features[col] = movie_data[col]
        
        # Convert to array in correct order
        feature_vector = np.array([features[col] for col in X_enhanced.columns]).reshape(1, -1)
        
        # Predict rating
        predicted_rating = model.predict(feature_vector)[0]
        
        # Get movie details
        movie_info = df[df['MovieID'] == movie_id].iloc[0]
        
        predictions.append({
            'MovieID': movie_id,
            'Title': movie_info['Title'],
            'Genres': movie_info['Genres'],
            'Predicted_Rating': predicted_rating
        })
    
    # Sort by predicted rating and get top N
    predictions_df = pd.DataFrame(predictions)
    top_recommendations = predictions_df.nlargest(top_n, 'Predicted_Rating')
    
    # Display recommendations
    print(f"{'Rank':<6} {'MovieID':<10} {'Predicted Rating':<18} {'Title':<40}")
    print(f"{'-'*6} {'-'*10} {'-'*18} {'-'*40}")
    
    for idx, row in enumerate(top_recommendations.itertuples(), 1):
        print(f"{idx:<6} {row.MovieID:<10} {row.Predicted_Rating:<18} {row.Title[:40]}")
    
    print(f"\n{'='*70}\n")
    
    return top_recommendations

In [25]:
# Example: Get recommendations for User ID 1 using both models

# Random Forest Recommendations
rf_recommendations = recommend_movies(1, rf_model, "Random Forest", top_n=5)

# KNN Recommendations  
knn_recommendations = recommend_movies(1, knn_model, "K-Nearest Neighbors", top_n=5)


🎬 Random Forest - Top 5 Movie Recommendations for User 1
User has rated: 53 movies
Evaluating: 3653 unrated movies



C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
[Parallel(n_jobs=12)]: Using backend ThreadingBackend with 12 concurrent workers.
[Parallel(n_jobs=12)]: Done  26 tasks      | elapsed:    0.0s
[Parallel(n_jobs=12)]: Done 100 out of 100 | elapsed:    0.0s finished
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
[Parallel(n_jobs=12)]: Using backend ThreadingBackend with 12 concurrent workers.
[Parallel(n_jobs=12)]: Done  26 tasks      | elapsed:    0.0s
[Parallel(n_jobs=12)]: Done 100 out of 100 | elapsed:    0.0s finished
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassif

Rank   MovieID    Predicted Rating   Title                                   
------ ---------- ------------------ ----------------------------------------
1      40         5                  Cry, the Beloved Country (1995)
2      50         5                  Usual Suspects, The (1995)
3      69         5                  Friday (1995)
4      110        5                  Braveheart (1995)
5      111        5                  Taxi Driver (1976)



🎬 K-Nearest Neighbors - Top 5 Movie Recommendations for User 1
User has rated: 53 movies
Evaluating: 3653 unrated movies



C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with featur

Rank   MovieID    Predicted Rating   Title                                   
------ ---------- ------------------ ----------------------------------------
1      6          5                  Heat (1995)
2      17         5                  Sense and Sensibility (1995)
3      28         5                  Persuasion (1995)
4      31         5                  Dangerous Minds (1995)
5      40         5                  Cry, the Beloved Country (1995)




C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with featur

In [26]:
# Display Top 5 Movie IDs side-by-side comparison
print("\n" + "="*70)
print("📊 COMPARISON: TOP 5 MOVIE IDs FROM BOTH MODELS")
print("="*70)

comparison_df = pd.DataFrame({
    'Rank': range(1, 6),
    'RF_MovieID': rf_recommendations['MovieID'].values,
    'RF_Pred_Rating': rf_recommendations['Predicted_Rating'].values.round(2),
    'KNN_MovieID': knn_recommendations['MovieID'].values,
    'KNN_Pred_Rating': knn_recommendations['Predicted_Rating'].values.round(2)
})

print(comparison_df.to_string(index=False))
print("="*70)


📊 COMPARISON: TOP 5 MOVIE IDs FROM BOTH MODELS
 Rank  RF_MovieID  RF_Pred_Rating  KNN_MovieID  KNN_Pred_Rating
    1          40               5            6                5
    2          50               5           17                5
    3          69               5           28                5
    4         110               5           31                5
    5         111               5           40                5


## 🎯 Try Different Users

You can test recommendations for any user by changing the user_id:

In [27]:
# Try recommendations for different user (change user_id to test)
test_user_id = 25  # Change this to any user ID

print(f"Testing recommendations for User {test_user_id}...\n")
recommend_movies(test_user_id, rf_model, "Random Forest", top_n=5)
recommend_movies(test_user_id, knn_model, "K-Nearest Neighbors", top_n=5)

Testing recommendations for User 25...


🎬 Random Forest - Top 5 Movie Recommendations for User 25
User has rated: 85 movies
Evaluating: 3621 unrated movies



C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
[Parallel(n_jobs=12)]: Using backend ThreadingBackend with 12 concurrent workers.
[Parallel(n_jobs=12)]: Done  26 tasks      | elapsed:    0.0s
[Parallel(n_jobs=12)]: Done 100 out of 100 | elapsed:    0.0s finished
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
[Parallel(n_jobs=12)]: Using backend ThreadingBackend with 12 concurrent workers.
[Parallel(n_jobs=12)]: Done  26 tasks      | elapsed:    0.0s
[Parallel(n_jobs=12)]: Done 100 out of 100 | elapsed:    0.0s finished
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but RandomForestClassif

Rank   MovieID    Predicted Rating   Title                                   
------ ---------- ------------------ ----------------------------------------
1      1          5                  Toy Story (1995)
2      40         5                  Cry, the Beloved Country (1995)
3      50         5                  Usual Suspects, The (1995)
4      69         5                  Friday (1995)
5      111        5                  Taxi Driver (1976)



🎬 K-Nearest Neighbors - Top 5 Movie Recommendations for User 25
User has rated: 85 movies
Evaluating: 3621 unrated movies



C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with featur

Rank   MovieID    Predicted Rating   Title                                   
------ ---------- ------------------ ----------------------------------------
1      1          5                  Toy Story (1995)
2      6          5                  Heat (1995)
3      17         5                  Sense and Sensibility (1995)
4      28         5                  Persuasion (1995)
5      31         5                  Dangerous Minds (1995)




C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(
C:\Users\adity\AppData\Roaming\Python\Python310\site-packages\sklearn\base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with featur

MovieID                         Title                       Genres  \
0         1              Toy Story (1995)  Animation|Children's|Comedy   
5         6                   Heat (1995)        Action|Crime|Thriller   
16       17  Sense and Sensibility (1995)                Drama|Romance   
27       28             Persuasion (1995)                      Romance   
30       31        Dangerous Minds (1995)                        Drama   

    Predicted_Rating  
0                  5  
5                  5  
16                 5  
27                 5  
30                 5